# Lab | Music recommendations

- First re-run everything in this notebook to ensure you're comfortable with the concepts of similar audio recommendation systems based on RAG.
- Using music datasets from [this](https://github.com/Yuan-ManX/ai-audio-datasets?tab=readme-ov-file#m) github repo, create a local RAG to recommend sons based on users preferences. Example dataset from that link could be [this](https://zenodo.org/records/5794629) Artificial multitrack audio data. Feel free to find you're own datasets online, or combine the dataset used in this lab with a few you found to make some recommendations.
- Go ahead and build something great in 4 hours.

This lab demonstrate how to use Pinecone as the vector DB within an audio search application. Audio search can be used to find songs and metadata within a catalog, finding similar sounds in an audio library, or detecting who's speaking in an audio file.

We will index a set of audio recordings as vector embeddings. These vector embeddings are rich, mathematical representations of the audio recordings, making it possible to determine how similar the recordings are to one another. We will then take some new (unseen) audio recording, search through the index to find the most similar matches, and play the returned audio in this notebook.

# Install Dependencies

In [1]:
!pip install librosa
!pip install panns-inference

In [2]:
!pip install -qU pinecone-client==3.1.0 panns-inference datasets librosa

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.0/211.0 kB 4.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 472.7/472.7 kB 16.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 7.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 8.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 11.6 MB/s eta 0:00:00


# Load Dataset

In this demo, we will use audio from the *ESC-50 dataset* — a labeled collection of 2000 environmental audio recordings, which are 5-second-long each. The dataset can be loaded from the HuggingFace model hub as follows:

In [3]:
from datasets import load_dataset

# load the dataset from huggingface model hub
data = load_dataset("ashraq/esc50", split="train")
data

README.md:   0%|          | 0.00/345 [00:00<?, ?B/s]

Repo card metadata block was not found. Setting CardData to empty.


dataset_infos.json:   0%|          | 0.00/1.61k [00:00<?, ?B/s]

(…)-00000-of-00002-2f1ab7b824ec751f.parquet:   0%|          | 0.00/387M [00:00<?, ?B/s]

(…)-00001-of-00002-27425e5c1846b494.parquet:   0%|          | 0.00/387M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/2000 [00:00<?, ? examples/s]

Dataset({
    features: ['filename', 'fold', 'target', 'category', 'esc10', 'src_file', 'take', 'audio'],
    num_rows: 2000
})

The audios in the dataset are sampled at 44100Hz and loaded into NumPy arrays. Let's take a look.

In [4]:
# select the audio feature and display top three
audios = data["audio"]
audios[:3]

[{'path': None,
  'array': array([0., 0., 0., ..., 0., 0., 0.]),
  'sampling_rate': 44100},
 {'path': None,
  'array': array([-0.01184082, -0.10336304, -0.14141846, ...,  0.06985474,
          0.04049683,  0.00274658]),
  'sampling_rate': 44100},
 {'path': None,
  'array': array([-0.00695801, -0.01251221, -0.01126099, ...,  0.215271  ,
         -0.00875854, -0.28903198]),
  'sampling_rate': 44100}]

We only need the Numpy arrays as these contain all of the audio data. We will later input these Numpy arrays directly into our embedding model to generate audio embeddings.

In [5]:
import numpy as np

# select only the audio data from the dataset and store in a numpy array
audios = np.array([a["array"] for a in data["audio"]])

# Load Audio Embedding Model

We will use an audio tagging model trained from *PANNs: Large-Scale Pretrained Audio Neural Networks for Audio Pattern Recognition* paper to generate our audio embeddings. We use the *panns_inference* Python package, which provides an easy interface to load and use the model.

In [6]:
from panns_inference import AudioTagging

# load the default model into the gpu.
model = AudioTagging(checkpoint_path=None, device='mps') # change device to cpu if a gpu is not available

Checkpoint path: /root/panns_data/Cnn14_mAP=0.431.pth
Using CPU.


/usr/local/lib/python3.10/dist-packages/panns_inference/inference.py:55: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(checkpoint_path, map_location=

## Initializing the Index

Now we need a place to store these embeddings and enable a efficient vector search through them all. To do that we use Pinecone, we can get a [free API key](https://app.pinecone.io/) and enter it below where we will initialize our connection to Pinecone and create a new index.

In [ ]:
from dotenv import load_dotenv, find_dotenv
import os
_ = load_dotenv(find_dotenv())

OPENAI_API_KEY  = os.getenv('OPENAI_API_KEY')
# initialize connection to pinecone (get API key at app.pinecone.io)
PINECONE_API_KEY = os.getenv("PINECONE_API_KEY") or "YOUR_API_KEY"

In [7]:
from google.colab import userdata

OPENAI_API_KEY = userdata.get('OPENAI_API_KEY')
PINECONE_API_KEY = userdata.get("PINECONE_API_KEY")

In [8]:
import os
from pinecone import Pinecone

# configure client
pc = Pinecone(api_key=PINECONE_API_KEY)

Now we setup our index specification, this allows us to define the cloud provider and region where we want to deploy our index. You can find a list of all [available providers and regions here](https://docs.pinecone.io/docs/projects).

In [9]:
from pinecone import ServerlessSpec

cloud = os.environ.get('PINECONE_CLOUD') or 'aws'
region = os.environ.get('PINECONE_REGION') or 'us-east-1'

spec = ServerlessSpec(cloud=cloud, region=region)

Create the index:

In [10]:
index_name = "audio-search-demo"

In [11]:
import time

# check if index already exists (it shouldn't if this is first time)
if index_name not in pc.list_indexes().names():
    # if does not exist, create index
    pc.create_index(
        index_name,
        dimension=2048,
        metric='cosine',
        spec=spec
    )
    # wait for index to be initialized
    while not pc.describe_index(index_name).status['ready']:
        time.sleep(1)

# connect to index
index = pc.Index(index_name)
# view index stats
index.describe_index_stats()

{'dimension': 2048,
 'index_fullness': 0.0,
 'namespaces': {'': {'vector_count': 768}},
 'total_vector_count': 768}

# Generate Embeddings and Upsert

Now we generate the embeddings using the audio embedding model. We must do this in batches as processing all items at once will exhaust machine memory limits and API request limits.

In [12]:
from tqdm.auto import tqdm

# we will use batches of 64
batch_size = 64

for i in tqdm(range(0, len(audios), batch_size)):
    # find end of batch
    i_end = min(i+batch_size, len(audios))
    # extract batch
    batch = audios[i:i_end]
    # generate embeddings for all the audios in the batch
    _, emb = model.inference(batch)
    # create unique IDs
    ids = [f"{idx}" for idx in range(i, i_end)]
    # add all to upsert list
    to_upsert = list(zip(ids, emb.tolist()))
    # upsert/insert these records to pinecone
    _ = index.upsert(vectors=to_upsert)

# check that we have all vectors in index
index.describe_index_stats()

  0%|          | 0/32 [00:00<?, ?it/s]

{'dimension': 2048,
 'index_fullness': 0.0,
 'namespaces': {'': {'vector_count': 2000}},
 'total_vector_count': 2000}

We now have *2000* audio records indexed in Pinecone, we're ready to begin querying.

# Querying

Let's first listen to an audio from our dataset. We will generate embeddings for the audio and use it to find similar audios from the Pinecone index.

In [13]:
from IPython.display import Audio, display

# we set an audio number to select from the dataset
audio_num = 400
# get the audio data of the audio number
query_audio = data[audio_num]["audio"]["array"]
# get the category of the audio number
category = data[audio_num]["category"]
# print the category and play the audio
print("Query Audio:", category)
Audio(query_audio, rate=44100)

Query Audio: car_horn


We have got the sound of a car horn. Let's generate an embedding for this sound.

In [14]:
# reshape query audio
query_audio = query_audio[None, :]
# get the embeddings for the audio from the model
_, xq = model.inference(query_audio)
xq.shape

(1, 2048)

We have now converted the audio into a 2048-dimension vector the same way we did for all the other audio we indexed. Let's use this to query our Pinecone index.

In [15]:
# query pinecone index with the query audio embeddings
results = index.query(vector=xq.tolist(), top_k=3)
results

{'matches': [{'id': '400', 'score': 1.00000012, 'values': []},
             {'id': '1667', 'score': 0.842124403, 'values': []},
             {'id': '1666', 'score': 0.831768632, 'values': []}],
 'namespace': '',
 'usage': {'read_units': 5}}

Notice that the top result is the audio number 400 from our dataset, which is our query audio (the most similar item should always be the query itself). Let's listen to the top three results.

In [16]:
# play the top 3 similar audios
for r in results["matches"]:
    # select the audio data from the databse using the id as an index
    a = data[int(r["id"])]["audio"]["array"]
    display(Audio(a, rate=44100))

We have great results, everything aligns with what seems to be a busy city street with car horns.

Let's write a helper function to run the queries using audio from our dataset easily. We do not need to embed these audio samples again as we have already, they are just stored in Pinecone. So, we specify the `id` of the query audio to search with and tell Pinecone to search with that.

In [17]:
def find_similar_audios(id):
    print("Query Audio:")
    # select the audio data from the databse using the id as an index
    query_audio = data[id]["audio"]["array"]
    # play the query audio
    display(Audio(query_audio, rate=44100))
    # query pinecone index with the query audio id
    result = index.query(id=str(id), top_k=5)
    print("Result:")
    # play the top 5 similar audios
    for r in result["matches"]:
        a = data[int(r["id"])]["audio"]["array"]
        display(Audio(a, rate=44100))

In [20]:
find_similar_audios(1642)

Output hidden; open in https://colab.research.google.com to view.

Here we return a set of revving motors (they seem to either be vehicles or lawnmowers).

In [21]:
find_similar_audios(452)

Output hidden; open in https://colab.research.google.com to view.

And now a more relaxing set of birds chirping in nature.

Let's use another audio sample from elsewhere (eg not this dataset) and see how the search performs with this.

In [ ]:
#!wget https://storage.googleapis.com/audioset/miaow_16k.wav

We can load the audio into a Numpy array as follows:

In [23]:
import librosa

a, _ = librosa.load("data/miaow_16k.wav", sr=44100)
Audio(a, rate=44100)

Now we generate the embeddings for this audio and query the Pinecone index.

In [24]:
# reshape query audio
query_audio = a[None, :]
# get the embeddings for the audio from the model
_, xq = model.inference(query_audio)

# query pinecone index with the query audio embeddings
results = index.query(vector=xq.tolist(), top_k=3)

# play the top 3 similar audios
for r in results["matches"]:
    a = data[int(r["id"])]["audio"]["array"]
    display(Audio(a, rate=44100))

Our audio search application has identified a set of similar cat sounds, which is excellent.

# Delete the Index

Delete the index once you are sure that you do not want to use it anymore. Once the index is deleted, you cannot use it again.

In [25]:
pc.delete_index(index_name)